In [9]:
import os
os.chdir(r'/Users/michalstypulkowski/Documents/Notebooks/TextMining')

import numpy as np
import pickle
from tqdm import trange, tqdm, tqdm_notebook

import re
from collections import defaultdict as dd
import nltk
import time
from sklearn.metrics.pairwise import linear_kernel

In [3]:
stop_words = set()
for line in open("data/stop_words.txt", 'r', encoding='utf8'):
    stop_words.add(line[:-1])
punctuation = set(["'", "(", ")", "-", "!", "[", "]", "–", "",
                   "&", "?", "''", ":", ';', '``', '.', '``', 
                   '„', '”', ',', '+', '=', '*'])

In [22]:
# word2vec = dd(list)
# for line in open(r'dane\wiki-forms-all-100-cbow-hs.txt', 'r', encoding='utf8'):
#     line = line[:-1].split(' ')
#     if len(line) != 101:
#         continue
#     word = line[0].lower()
#     embs = [float(val) for val in line[1:]]
#     word2vec[word] = embs

In [4]:
# if not os.path.exists('.cache'):
#     os.makedirs('.cache')
    
# with open(f'.cache/word2vec.pickle', 'wb') as file:
#     pickle.dump(word2vec, file, protocol=pickle.HIGHEST_PROTOCOL)
    
with open(f'.cache/word2vec.pickle', 'rb') as file:
    word2vec = pickle.load(file)

In [6]:
wiki_map = dd(list)
header = None
for i, line in enumerate(open(r'data/poczatki_wikipediowe.txt', 'r', encoding='utf-8')):
    if line == '\n':
        continue
        
    if line[:3] == '###':
        line = line.split(' ')[1:]
        if len(line) > 1:
            header = None
            continue
        header = line[0][:-1]
            
    elif header is not None:
        line = nltk.word_tokenize(line)
        clean_line = []
        for token in line:
            if token in punctuation or token in stop_words:
                continue
            if token[0] == "'":
                token = token[1:]
            clean_line.append(token)
        wiki_map[header] = clean_line

In [7]:
if not os.path.exists('.cache'):
    os.makedirs('.cache')
    
with open(f'.cache/wiki_map.pickle', 'wb') as file:
    pickle.dump(wiki_map, file, protocol=pickle.HIGHEST_PROTOCOL)
    
# with open(f'.cache/wiki_map.pickle', 'rb') as file:
#     wiki_map = pickle.load(file)

In [10]:
threshold = 20
synonyms = dd(list)
for key in tqdm_notebook(wiki_map):
    key_emb = word2vec[key.lower()]
    if key_emb == []:
        continue

    synonyms[key] = []
    for word in wiki_map[key]:
        if word.lower() == key.lower():
            continue
        word_emb = word2vec[word.lower()]
        if word_emb == []:
            continue
        
        distance = linear_kernel(np.array(word_emb).reshape(1,-1), np.array(key_emb).reshape(1,-1))
        if distance > threshold:
            synonyms[key].append(word)

In [11]:
for key in synonyms:
    if synonyms[key] != []:
        print(key, np.unique(np.array(synonyms[key])))

Astronomia ['Astronomię' 'Wszechświatem' 'ewolucji' 'greki' 'gwiazda' 'kosmicznej'
 'materii' 'nauka']
AWK ['programowania']
Alergologia ['dziedzina']
ASCII ['32' 'Code' 'Information' 'Litery' 'Przykładowo' 'Standard' 'alfabetu'
 'angielskiego' 'cyfry' 'drukowane' 'innym' 'kod' 'kodowana' 'liczby'
 'litera' 'literom' 'spacji' 'sterującym' 'zakresu' 'zbiór' 'znak' 'znaki'
 'znakom' 'znaków']
Atom ['Atomy' 'Neutrony' 'atomu' 'chemiczne' 'cząstkami' 'elektronów' 'jądra'
 'jądro' 'jądrze' 'materii' 'najmniejszy' 'neutrony' 'niepodzielny'
 'nukleony' 'protony' 'składnik' 'teorię' 'właściwości']
Aksjomat ['Euklidesa' 'aksjomatu' 'aksjomaty' 'danej' 'definicja' 'dowodzi'
 'godność' 'gr' 'logiki' 'matematyce' 'matematycznej' 'oczywistość'
 'pewnik' 'pewność' 'podstawowych' 'pojęć' 'postulat' 'prawdziwe'
 'przyjmowane' 'teorii' 'uznawano' 'zdania']
Arytmetyka ['Historia' 'arytmetyki' 'dodawania' 'elementarna' 'liczba' 'liczbach'
 'matematyki' 'najstarsza' 'opisujących' 'podstawowe' 'pojęciami' 